this project intended to use geospatial analysis in Toronto city to cluster the neighborhood of Toronto to take decision where to open new branch for retail based on previous success in one of Toronto neighborhood. The main problem for retail is accessibility. Some retails thrive by locating near each other and some retails prefer areas where there is high pedestrian footage or high vehicle traffic density.

Through out this project we tried to cluster Toronto neighborhood by the category of retails and entrainment facility in the neighborhood combined with the vehicles and pedestrians’ traffic in that neighborhood using ten different clusters. So, the business owners from the area where direct competitors achieve success or in neighborhood where they achieved success before they can choose new places to expand in the city from the same cluster.

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
!conda install  -c conda-forge shapely --yes
!pip install msgpack
!pip install shapely
import folium # map rendering library
from shapely.geometry import Point # Point class
from shapely.geometry import shape # shape() is a function to convert geo objects through the interface
from bs4 import BeautifulSoup

print('Libraries imported.')

Solving environment: done

# All requested packages already installed.

Solving environment: done

# All requested packages already installed.

Solving environment: done

# All requested packages already installed.

Libraries imported.


getting the Toronto neighborhood boundaries from Toronto open data[the link](https://www.toronto.ca/city-government/data-research-maps/open-data/open-data-catalogue/#a45bd45a-ede8-730e-1abc-93105b2c439f "Logo Title Text 1") () and put it in Geodataframe 

In [3]:
!pip install git+git://github.com/geopandas/geopandas.git
import geopandas
gdf = geopandas.read_file('NEIGHBORHOODS_WGS84.shp')

  Cloning git://github.com/geopandas/geopandas.git to /tmp/pip-req-build-gb6555yn
  Running setup.py bdist_wheel for geopandas ... done
  Stored in directory: /tmp/pip-ephem-wheel-cache-88a1v_un/wheels/91/24/71/376c9c67192694168352afcccc2d264248f7e2cc6192997186
Successfully built geopandas


Cleaning the GeoDataframe and renaming coloumns

In [4]:
gdf['AREA_NAME'] = gdf['AREA_NAME'].map(lambda x: x.rstrip('(0123456789)'))
gdf= gdf.rename(index=str, columns={'AREA_NAME': 'Neighbourhood'})
gdf.head(3)


AREA_S_CD             Neighbourhood  \
0       097           Yonge-St.Clair    
1       027  York University Heights    
2       038         Lansing-Westgate    

                                            geometry  
0  POLYGON ((-79.39119482700001 43.681081124, -79...  
1  POLYGON ((-79.505287916 43.759873494, -79.5048...  
2  POLYGON ((-79.439984311 43.761557655, -79.4400...

Assign point inside the Neighbourhood boundaries so we can use it in foursquare

In [5]:
!pip install geojson
import geojson
import shapely.geometry
gdf['Latitude'] = 0
gdf['longitude'] = 0
for i, lat, lng, geometry  in zip(gdf.index, gdf['Latitude'], gdf['longitude'], gdf['geometry']):
    boundary =shapely.geometry.asShape( gdf.loc[i]['geometry']) # get a boundary polygon
    point=shape(boundary.centroid)
    point=geojson.Feature(geometry=point, properties={})
    gdf.loc[i,'Latitude'] = point['geometry']['coordinates'][1]
    gdf.loc[i,'longitude'] =point['geometry']['coordinates'][0]

In [6]:
gdf.shape

(140, 5)

ploting the point for the Neighbourhood

In [7]:
address = 'Toronto, ON'

geolocator = Nominatim()
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
map_Toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, Neighbourhood, Area in zip(gdf['Latitude'], gdf['longitude'], gdf['Neighbourhood'], gdf['AREA_S_CD']):
    label = '{}, {}'.format(Neighbourhood, Area)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_Toronto)  
    
map_Toronto

/home/jupyterlab/conda/lib/python3.6/site-packages/geopy/geocoders/osm.py:143: UserWarning: Using Nominatim with the default "geopy/1.17.0" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  UserWarning


reading the data for the Traffic density for Pedestrian  and vehicles

In [57]:
df1 = pd.ExcelFile('8hrVeh&PedVolume_6-Mar-2018.xlsx').parse('Total TMM count')
df1=df1.rename(index=str, columns={'Latitude': 'Lat','Longitude': 'Longt'})
df1.head(3)

TCS #       Main Midblock Route   Side 1 Route Side 2 Route  \
0      2  JARVIS ST            NaN     FRONT ST E          NaN   
1      3  KING ST E            NaN      JARVIS ST          NaN   
2      4  JARVIS ST            NaN  ADELAIDE ST E          NaN   

  Activation Date        Lat      Longt Count Date  8 Peak Hr Vehicle Volume  \
0      11/15/1948  43.649418 -79.371446 2017-06-21                     15662   
1      08/23/1950  43.650461 -79.371924 2016-09-17                     12960   
2      09/12/1958  43.651534 -79.372360 2016-11-08                     17770   

   8 Peak Hr Pedestrian Volume  
0                        13535  
1                         7333  
2                         7083

plotting the data for the traffic

In [75]:
from folium.plugins import HeatMap
folium_map1 = folium.Map(location=[latitude, longitude],
                        zoom_start=11,
                        tiles="CartoDB dark_matter")


for index, row in df1.iterrows():
    Vhe = row["8 Peak Hr Vehicle Volume"]
    ped = row["8 Peak Hr Pedestrian Volume"]
    radius = Vhe/4000
    radius1 = ped/900                  
    color="#E37222" # tangerine
    color1="#0A8A9F" # teal
    
    folium.CircleMarker(location=(row["Lat"],
                                  row["Longt"]),
                        radius=radius1,
                        color=color1,
                        fill=True).add_to(folium_map1)
    folium.CircleMarker(location=(row["Lat"],
                                  row["Longt"]),
                        radius=radius,
                        color=color,
                        fill=True).add_to(folium_map1)
folium_map1

adding the traffic data to the each Neighbourhood by checking the traffic light latitude and longitide if it 
inside the boundary and create coloum with  sum for pedestrian and vehicle

In [9]:
gdf['Vehicle_density'] = 0
gdf['Pedestrian_dens'] = 0
for i, lat, long, Vehicle_dens,  Pedestrian_dens  in zip(df1.index, df1['Lat'], df1['Longt'], df1['8 Peak Hr Vehicle Volume'],df1['8 Peak Hr Pedestrian Volume']):
    pt=shapely.geometry.Point(df1.loc[i]['Longt'],df1.loc[i]['Lat'])
    Vehicle_dens=df1.loc[i]['8 Peak Hr Vehicle Volume']
    Pedestrian_dens=df1.loc[i]['8 Peak Hr Pedestrian Volume']
    for i, geometry  in zip(gdf.index, gdf['geometry']):
        boundary =shapely.geometry.asShape( gdf.loc[i]['geometry']) # get a boundary polygon
        if pt.within(boundary):
            gdf.loc[i,'Vehicle_density'] = gdf.loc[i,'Vehicle_density']+ Vehicle_dens
            gdf.loc[i,'Pedestrian_dens'] = gdf.loc[i,'Pedestrian_dens']+Pedestrian_dens
            break;


In [61]:
gdf.head(2)

AREA_S_CD             Neighbourhood  \
0       097           Yonge-St.Clair    
1       027  York University Heights    

                                            geometry   Latitude  longitude  \
0  POLYGON ((-79.39119482700001 43.681081124, -79...  43.687859 -79.397871   
1  POLYGON ((-79.505287916 43.759873494, -79.5048...  43.765738 -79.488883   

   Vehicle_density  Pedestrian_dens  
0           183536            16587  
1           725619            43226

creating calling function for foursquare to get the venues Data and call the function

In [14]:
CLIENT_ID = 'WZLVJPFDK44S0J1XC4SQCOEGLS34UQYOQLXRAGE2IA3UUT4L' # your Foursquare ID
CLIENT_SECRET = 'BPEX5BZV5TQQOBHQ4ZZN04HEV0LCCUT1AC4JYTQCNV53LDCJ' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT=400
def getNearbyVenues(names, latitudes, longitudes, radius=5000):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
        
        
        for i in range(1,50):
            current_radius = radius + 50 * (i - 1)
            # create the API request URL
            url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
                CLIENT_ID, 
                CLIENT_SECRET, 
                VERSION, 
                lat, 
                lng, 
                current_radius, 
                LIMIT)

            # make the GET request
            groups = requests.get(url).json()["response"]["groups"]

            selected_group = []
            for group in groups:
                if len(group) > len(selected_group):
                    selected_group = group
                  

            venue_list = []
            if len(selected_group) > 0:
                results = selected_group['items']

                # return only relevant information for each nearby venue
                venue_list = [(
                    name, 
                    lat, 
                    lng, 
                    v['venue']['id'], 
                    v['venue']['name'], 
                    v['venue']['location']['lat'], 
                    v['venue']['location']['lng'],  
                    v['venue']['categories'][0]['name'],
                    current_radius
                ) for v in results if v['venue']['categories']]
            
            if len(venue_list) > 10:
                venues_list.append(venue_list)
                break

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'ID',
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category',
                  'Explore Radius']
    
    return(nearby_venues)

In [15]:
Tornto_venues = getNearbyVenues(names=gdf['Neighbourhood'],
                                   latitudes=gdf['Latitude'],
                                   longitudes=gdf['longitude']
                                  )


Yonge-St.Clair 
York University Heights 
Lansing-Westgate 
Yorkdale-Glen Park 
Stonegate-Queensway 
Tam O'Shanter-Sullivan 
The Beaches 
Thistletown-Beaumond Heights 
Thorncliffe Park 
Danforth East York 
Humewood-Cedarvale 
Islington-City Centre West 
Danforth 
Rustic 
Scarborough Village 
South Parkdale 
South Riverdale 
St.Andrew-Windfields 
Taylor-Massey 
Humber Summit 
Humbermede 
Centennial Scarborough 
Church-Yonge Corridor 
Clairlea-Birchmount 
Cliffcrest 
Flemingdon Park 
Corso Italia-Davenport 
Ionview 
Junction Area 
Broadview North 
Princess-Rosethorn 
North Riverdale 
Etobicoke West Mall 
Forest Hill North 
Glenfield-Jane Heights 
Greenwood-Coxwell 
Guildwood 
Trinity-Bellwoods 
Victoria Village 
Waterfront Communities-The Island 
West Hill 
West Humber-Clairville 
Westminster-Branson 
Kennedy Park 
Kingsview Village-The Westway 
Bayview Woods-Steeles 
Clanton Park 
Keelesdale-Eglinton West 
O'Connor-Parkview 
Old East York 
Casa Loma 
Kensington-Chinatown 
Kingsway South 

In [16]:
Tornto_venues.shape

(13964, 9)

In [17]:
df3=Tornto_venues.copy()

In [18]:
df5=df3.copy()

because the Neighbourhood boundaries is  olygon ome time when we use the foursquarethe api take point and radius 
to get near by venues so some time the api feedback assign venues to  near Neighborhood so we create for loop
to check the result and to asign it to the right Neighborhood

In [19]:
df5['Neighborhood'] = 0
df5['Venue'] = 0
df5['Venue Latitude'] = 0
df5['Venue Longitude'] = 0
df5['Venue Category'] = 0
z=0
for i, lat, long, Venue, Category  in zip(df3.index, df3['Venue Latitude'], df3['Venue Longitude'], df3['Venue'],df3['Venue Category']):
    pt=shapely.geometry.Point(df3.loc[i]['Venue Longitude'],df3.loc[i]['Venue Latitude'])
    for x, geometry  in zip(gdf.index, gdf['geometry']):
        boundary =shapely.geometry.asShape( gdf.loc[x]['geometry']) # get a boundary polygon
        if pt.within(boundary):
            df5.loc[i,'Neighborhood'] = gdf.loc[x]['Neighbourhood']
            df5.loc[i,'Venue'] = df3.loc[i]['Venue']
            df5.loc[i,'Venue Latitude'] = df3.loc[i]['Venue Latitude']
            df5.loc[i,'Venue Longitude'] = df3.loc[i]['Venue Longitude']
            df5.loc[i,'Venue Category'] = df3.loc[i]['Venue Category']
            z=z+1
            break;

print(z)

13176


In [60]:
df5.head(10)

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0       Yonge-St.Clair               43.687859              -79.397871   
1  Rosedale-Moore Park               43.687859              -79.397871   
2  Rosedale-Moore Park               43.687859              -79.397871   
3            Casa Loma               43.687859              -79.397871   
4                Annex               43.687859              -79.397871   
5  Rosedale-Moore Park               43.687859              -79.397871   
6            Casa Loma               43.687859              -79.397871   
7                Annex               43.687859              -79.397871   
8                Annex               43.687859              -79.397871   
9                Annex               43.687859              -79.397871   

                         ID                Venue  Venue Latitude  \
0  4f89f40ee4b0ab0c1b90e2c5         Waxon Waxbar       43.682824   
1  4aea405ef964a52082ba21e3                 LCBO       43.681497   
2  5282572111d2f33612220715        Boxcar Social       43.681750   
3  4ad4c061f964a520a5f720e3          Scaramouche       43.681293   
4  52ced2c9498e67e1059cf3b2  Greenhouse Juice Co       43.679101   
5  4ad88fa9f964a520511221e3          Black Camel       43.677016   
6  4bef48fcc80dc9284ec827e3            Casa Loma       43.677934   
7  4ad4c05cf964a520f1f520e3   L'Unita Restaurant       43.674387   
8  4ad4c061f964a520a3f720e3               Joso's       43.674835   
9  50abfac3e4b05922967ebe89          Rose & Sons       43.675668   

   Venue Longitude            Venue Category  Explore Radius  
0       -79.391971                       Spa            5000  
1       -79.391261              Liquor Store            5000  
2       -79.391447               Coffee Shop            5000  
3       -79.399492         French Restaurant            5000  
4       -79.390686                 Juice Bar            5000  
5       -79.389367                 BBQ Joint            5000  
6       -79.409521                    Castle            5000  
7       -79.396488        Italian Restaurant            5000  
8       -79.396171  Mediterranean Restaurant            5000  
9       -79.403617       American Restaurant            5000

clening the data frame 

In [21]:
df6=df5.copy()
df6.to_csv('out2.csv')
df6 = df6[df6.Neighborhood != 0]
df6.head(3)

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0       Yonge-St.Clair               43.687859              -79.397871   
1  Rosedale-Moore Park               43.687859              -79.397871   
2  Rosedale-Moore Park               43.687859              -79.397871   

                         ID          Venue  Venue Latitude  Venue Longitude  \
0  4f89f40ee4b0ab0c1b90e2c5   Waxon Waxbar       43.682824       -79.391971   
1  4aea405ef964a52082ba21e3           LCBO       43.681497       -79.391261   
2  5282572111d2f33612220715  Boxcar Social       43.681750       -79.391447   

  Venue Category  Explore Radius  
0            Spa            5000  
1   Liquor Store            5000  
2    Coffee Shop            5000

get the data for the point of interest from the city of Toronto open data
[here](https://www.toronto.ca/city-government/data-research-maps/open-data/open-data-catalogue/#bed7e463-f317-ec5f-5b4b-775648011ff9 "Logo Title Text 1")

In [59]:
dbf = Dbf5('PLACES_OF_INTEREST_WGS84.dbf',codec='ISO-8859-1')
test2 = dbf.to_dataframe()
test2.head(3)

ID ADDR_INFO                                   TITLE         CATEGORY  \
0  38       NaN                          Downsview Park    Featured Park   
1  40       NaN  Elgin and Winter Garden Theatre Centre  Performing Arts   
2  41       NaN                      Eskimo Art Gallery          Gallery   

             PHONE  EMAIL                                       WEBSITE  \
0     416-952-2222    NaN                          www.downsviewpark.ca   
1     416-314-2901    NaN  http://www.heritagetrust.on.ca/ewg/home.aspx   
2  1 -877-364-6845    NaN                     http://www.eskimoart.com/   

             ADDRESS POSTAL_CD           X            Y  LONGITUDE   LATITUDE  \
0    35 Carl Hall Rd   M3K 2B6  306462.998  4844967.208 -79.479160  43.746667   
1       189 Yonge St   M5B 1M4  314528.372  4834575.370 -79.379204  43.653065   
2  8 Case Goods Lane   M5A 3C4  316166.580  4834235.874 -79.358899  43.649977   

   OBJECTID                    SRC_ADDRSS  LEVEL  \
0        38             35 Carl Hall Road      3   
1        40              189 Yonge Street      2   
2        41  8 Case Goods Lane, Suite 220      4   

                                          DESCRIPTIO  
0  The vast green space allows for an array of sm...  
1  The Elgin and Winter Garden Theatre features t...  
2  Located in the Distillery District, the Eskimo...

assign the points  th right Neighbourhood and added to the venues database

In [23]:
z=0
for i, lat, long, Venue, Category  in zip(test2.index, test2['LATITUDE'], test2['LONGITUDE'], test2['TITLE'],test2['CATEGORY']):
    pt=shapely.geometry.Point(test2.iloc[i]['LONGITUDE'],test2.loc[i]['LATITUDE'])
    for x, geometry  in zip(gdf.index, gdf['geometry']):
        boundary =shapely.geometry.asShape( gdf.loc[x]['geometry']) # get a boundary polygon
        if pt.within(boundary):
            venue_list = [( gdf.loc[x]['Neighbourhood'],0,0,i, test2.loc[i]['TITLE'], test2.loc[i]['LATITUDE'], test2.loc[i]['LONGITUDE'], test2.loc[i]['CATEGORY'],0)]
            df6.append(venue_list)
            z=z+1
            break;

print(z)

/home/jupyterlab/conda/lib/python3.6/site-packages/pandas/core/indexes/api.py:107: RuntimeWarning: '<' not supported between instances of 'str' and 'int', sort order is undefined for incomparable objects
  result = result.union(other)


179


cleaning the data

In [24]:
df7=df6.drop_duplicates(subset=['ID','Venue'], keep="last").reset_index(drop=True)
df7=df7.drop(['Neighborhood Latitude', 'Neighborhood Longitude','ID','Explore Radius'], axis=1)
df7.tail(3)


Neighborhood                   Venue  \
1915                        Junction Area                     LCBO   
1916  Dovercourt-Wallace Emerson-Junction       Christie Pits Park   
1917                        Junction Area   When the Pig Came Home   

      Venue Latitude  Venue Longitude Venue Category  
1915       43.670436       -79.473005   Liquor Store  
1916       43.664177       -79.420466           Park  
1917       43.665285       -79.470512  Deli / Bodega

In [25]:
df7.head(2)

Neighborhood                Venue  Venue Latitude  \
0  York University Heights   Walmart Supercentre       43.757685   
1  York University Heights             Montana's       43.786645   

   Venue Longitude Venue Category  
0       -79.489131  Big Box Store  
1       -79.471494     Steakhouse

during checking the data after cleaning I realized that one Neighborhood doesnt have venues o i added null
value to it 

In [26]:
df7.loc[-1] = ['Rustic', np.NaN, np.NaN, np.NaN, np.NaN] 
df7.tail(3)


Neighborhood                   Venue  \
 1916  Dovercourt-Wallace Emerson-Junction       Christie Pits Park   
 1917                        Junction Area   When the Pig Came Home   
-1                                   Rustic                     NaN   

       Venue Latitude  Venue Longitude Venue Category  
 1916       43.664177       -79.420466           Park  
 1917       43.665285       -79.470512  Deli / Bodega  
-1                NaN              NaN            NaN

creating function to retu most common venues 

In [27]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [31]:
num_top_venues = 10


indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head(3)

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0               Agincourt North   Fast Food Restaurant        Sandwich Place   
1  Agincourt South-Malvern West   Gym / Fitness Center           Coffee Shop   
2                     Alderwood         Discount Store                   Pub   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0        Discount Store  Caribbean Restaurant    Chinese Restaurant   
1    Chinese Restaurant  Caribbean Restaurant        Breakfast Spot   
2   Moroccan Restaurant                   Gym         Grocery Store   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0     Indian Restaurant        Chocolate Shop             Juice Bar   
1     Indian Restaurant              Pharmacy            Restaurant   
2           Pizza Place     Electronics Store            Donut Shop   

  9th Most Common Venue       10th Most Common Venue  
0           Supermarket                     Pharmacy  
1                 Diner               Sandwich Place  
2   Dumpling Restaurant  Eastern European Restaurant

creating Datatrame for Neighborhood with the categrory type

In [29]:
Toronto_onehot = pd.get_dummies(df7[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
Toronto_onehot['Neighborhood'] = df7['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [Toronto_onehot.columns[-1]] + list(Toronto_onehot.columns[:-1])
Toronto_onehot = Toronto_onehot[fixed_columns]


In [30]:
toronto_grouped = Toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped.head(10)

Neighborhood  Zoo Exhibit  Adult Boutique  \
0               Agincourt North           0.0             0.0   
1  Agincourt South-Malvern West           0.0             0.0   
2                     Alderwood           0.0             0.0   
3                         Annex           0.0             0.0   
4             Banbury-Don Mills           0.0             0.0   
5                Bathurst Manor           0.0             0.0   
6           Bay Street Corridor           0.0             0.0   
7               Bayview Village           0.0             0.0   
8         Bayview Woods-Steeles           0.0             0.0   
9          Bedford Park-Nortown           0.0             0.0   

   Afghan Restaurant  African Restaurant  American Restaurant  Aquarium  \
0                0.0                 0.0             0.000000       0.0   
1                0.0                 0.0             0.000000       0.0   
2                0.0                 0.0             0.000000       0.0   
3                0.0                 0.0             0.043478       0.0   
4                0.0                 0.0             0.000000       0.0   
5                0.0                 0.0             0.000000       0.0   
6                0.0                 0.0             0.055556       0.0   
7                0.0                 0.0             0.000000       0.0   
8                0.0                 0.0             0.000000       0.0   
9                0.0                 0.0             0.000000       0.0   

   Art Gallery  Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0          0.0                  0.0          0.000000                 0.0   
1          0.0                  0.0          0.041667                 0.0   
2          0.0                  0.0          0.000000                 0.0   
3          0.0                  0.0          0.000000                 0.0   
4          0.0                  0.0          0.025641                 0.0   
5          0.0                  0.0          0.000000                 0.0   
6          0.0                  0.0          0.000000                 0.0   
7          0.0                  0.0          0.000000                 0.0   
8          0.0                  0.0          0.000000                 0.0   
9          0.0                  0.0          0.000000                 0.0   

   Auto Dealership  Automotive Shop  BBQ Joint  Bagel Shop    Bakery  Bank  \
0              0.0              0.0        0.0         0.0  0.000000   0.0   
1              0.0              0.0        0.0         0.0  0.041667   0.0   
2              0.0              0.0        0.0         0.0  0.000000   0.0   
3              0.0              0.0        0.0         0.0  0.000000   0.0   
4              0.0              0.0        0.0         0.0  0.025641   0.0   
5              0.0              0.0        0.0         0.0  0.000000   0.0   
6              0.0              0.0        0.0         0.0  0.000000   0.0   
7              0.0              0.0        0.0         0.0  0.000000   0.0   
8              0.0              0.0        0.0         0.0  0.000000   0.0   
9              0.0              0.0        0.0         0.1  0.000000   0.0   

        Bar  Baseball Field  Baseball Stadium  Basketball Court  \
0  0.000000             0.0               0.0               0.0   
1  0.000000             0.0               0.0               0.0   
2  0.000000             0.0               0.0               0.0   
3  0.000000             0.0               0.0               0.0   
4  0.025641             0.0               0.0               0.0   
5  0.000000             0.0               0.0               0.0   
6  0.000000             0.0               0.0               0.0   
7  0.000000             0.0               0.0               0.0   
8  0.000000             0.0               0.0               0.0   
9  0.000000             0.0               0.0               0.0   

   Basketball Stadium  Beach  Bee

In [33]:
gdf.head(2)

AREA_S_CD             Neighbourhood  \
0       097           Yonge-St.Clair    
1       027  York University Heights    

                                            geometry   Latitude  longitude  \
0  POLYGON ((-79.39119482700001 43.681081124, -79...  43.687859 -79.397871   
1  POLYGON ((-79.505287916 43.759873494, -79.5048...  43.765738 -79.488883   

   Vehicle_density  Pedestrian_dens  
0           183536            16587  
1           725619            43226

add the veicle and pedesain density to ata frame

In [34]:
toronto_grouped['Vehicle_density'] = 0
toronto_grouped['Pedestrian_dens'] = 0
for x, Neighbourhood  in zip(gdf.index, gdf['Neighbourhood']):
    Vehicle_dens=gdf.loc[x]['Vehicle_density']
    Pedestrian_dens=gdf.loc[x]['Pedestrian_dens']
    for i, Neighborhood  in zip(toronto_grouped.index, toronto_grouped['Neighborhood']):
        if gdf.loc[x]['Neighbourhood']== toronto_grouped.loc[i]['Neighborhood'] :
            toronto_grouped.loc[i,'Vehicle_density'] =Vehicle_dens 
            toronto_grouped.loc[i,'Pedestrian_dens'] =Pedestrian_dens
            z=z+1
            break;

print(z)

318


In [35]:
toronto_grouped.head(3)

Neighborhood  Zoo Exhibit  Adult Boutique  \
0               Agincourt North           0.0             0.0   
1  Agincourt South-Malvern West           0.0             0.0   
2                     Alderwood           0.0             0.0   

   Afghan Restaurant  African Restaurant  American Restaurant  Aquarium  \
0                0.0                 0.0                  0.0       0.0   
1                0.0                 0.0                  0.0       0.0   
2                0.0                 0.0                  0.0       0.0   

   Art Gallery  Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0          0.0                  0.0          0.000000                 0.0   
1          0.0                  0.0          0.041667                 0.0   
2          0.0                  0.0          0.000000                 0.0   

   Auto Dealership  Automotive Shop  BBQ Joint  Bagel Shop    Bakery  Bank  \
0              0.0              0.0        0.0         0.0  0.000000   0.0   
1              0.0              0.0        0.0         0.0  0.041667   0.0   
2              0.0              0.0        0.0         0.0  0.000000   0.0   

   Bar  Baseball Field  Baseball Stadium  Basketball Court  \
0  0.0             0.0               0.0               0.0   
1  0.0             0.0               0.0               0.0   
2  0.0             0.0               0.0               0.0   

   Basketball Stadium  Beach  Beer Bar  Beer Store  Big Box Store  Bike Shop  \
0                 0.0    0.0       0.0         0.0            0.0        0.0   
1                 0.0    0.0       0.0         0.0            0.0        0.0   
2                 0.0    0.0       0.0         0.0            0.0        0.0   

   Bistro  Bookstore  Boutique  Bowling Alley  Brazilian Restaurant  \
0     0.0        0.0       0.0            0.0                   0.0   
1     0.0        0.0       0.0            0.0                   0.0   
2     0.0        0.0       0.0            0.0                   0.0   

   Breakfast Spot  Brewery  Bridal Shop  Bridge  Bubble Tea Shop  Building  \
0        0.000000      0.0          0.0     0.0              0.0       0.0   
1        0.083333      0.0          0.0     0.0              0.0       0.0   
2        0.000000      0.0          0.0     0.0              0.0       0.0   

   Burger Joint  Burrito Place  Butcher  Café  Cajun / Creole Restaurant  \
0           0.0            0.0      0.0   0.0                        0.0   
1           0.0            0.0      0.0   0.0                        0.0   
2           0.0            0.0      0.0   0.0                        0.0   

   Campground  Candy Store  Cantonese Restaurant  Caribbean Restaurant  \
0         0.0          0.0              0.000000              0.100000   
1         0.0          0.0              0.041667              0.083333   
2         0.0          0.0              0.000000              0.000000   

   Casino  Castle  Chinese Restaurant  Chocolate Shop  Churrascaria  Circus  \
0     0.0     0.0            0.100000             0.1           0.0     0.0   
1     0.0     0.0            0.083333             0.0           0.0     0.0   
2     0.0     0.0            0.000000             0.0           0.0     0.0   

   Climbing Gym  Clothing Store  Cocktail Bar  Coffee Shop  \
0           0.0             0.0           0.0     0.000000   
1           0.0             0.0           0.0     0.083333   
2           0.0             0.0           0.0     0.000000   

   College Rec Center  Comedy Club  Comfort Food Restaurant  Comic Shop  \
0                 0.0          0.0                      0.0         0.0   
1                 0.0          0.0                      0.0         0.0   
2                 0.0          0.0                      0.0         0.0   

   Concert Hall  Convenience Store  Cosmetics Shop  Creperie  \
0           0.0                0.0             0.0       0.0   
1           0.0                0.0             0.0       0.0   
2      

normalize the values for the traffic Data ing sklearn

In [36]:
from sklearn import preprocessing
x = toronto_grouped[['Vehicle_density']].values.astype(float)

# Create a minimum and maximum processor object
min_max_scaler = preprocessing.MinMaxScaler()

# Create an object to transform the data to fit minmax processor
x_scaled = min_max_scaler.fit_transform(x)

# Run the normalizer on the dataframe
toronto_grouped['Vehicle_density'] = pd.DataFrame(x_scaled)

In [37]:
toronto_grouped.head(3)

Neighborhood  Zoo Exhibit  Adult Boutique  \
0               Agincourt North           0.0             0.0   
1  Agincourt South-Malvern West           0.0             0.0   
2                     Alderwood           0.0             0.0   

   Afghan Restaurant  African Restaurant  American Restaurant  Aquarium  \
0                0.0                 0.0                  0.0       0.0   
1                0.0                 0.0                  0.0       0.0   
2                0.0                 0.0                  0.0       0.0   

   Art Gallery  Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0          0.0                  0.0          0.000000                 0.0   
1          0.0                  0.0          0.041667                 0.0   
2          0.0                  0.0          0.000000                 0.0   

   Auto Dealership  Automotive Shop  BBQ Joint  Bagel Shop    Bakery  Bank  \
0              0.0              0.0        0.0         0.0  0.000000   0.0   
1              0.0              0.0        0.0         0.0  0.041667   0.0   
2              0.0              0.0        0.0         0.0  0.000000   0.0   

   Bar  Baseball Field  Baseball Stadium  Basketball Court  \
0  0.0             0.0               0.0               0.0   
1  0.0             0.0               0.0               0.0   
2  0.0             0.0               0.0               0.0   

   Basketball Stadium  Beach  Beer Bar  Beer Store  Big Box Store  Bike Shop  \
0                 0.0    0.0       0.0         0.0            0.0        0.0   
1                 0.0    0.0       0.0         0.0            0.0        0.0   
2                 0.0    0.0       0.0         0.0            0.0        0.0   

   Bistro  Bookstore  Boutique  Bowling Alley  Brazilian Restaurant  \
0     0.0        0.0       0.0            0.0                   0.0   
1     0.0        0.0       0.0            0.0                   0.0   
2     0.0        0.0       0.0            0.0                   0.0   

   Breakfast Spot  Brewery  Bridal Shop  Bridge  Bubble Tea Shop  Building  \
0        0.000000      0.0          0.0     0.0              0.0       0.0   
1        0.083333      0.0          0.0     0.0              0.0       0.0   
2        0.000000      0.0          0.0     0.0              0.0       0.0   

   Burger Joint  Burrito Place  Butcher  Café  Cajun / Creole Restaurant  \
0           0.0            0.0      0.0   0.0                        0.0   
1           0.0            0.0      0.0   0.0                        0.0   
2           0.0            0.0      0.0   0.0                        0.0   

   Campground  Candy Store  Cantonese Restaurant  Caribbean Restaurant  \
0         0.0          0.0              0.000000              0.100000   
1         0.0          0.0              0.041667              0.083333   
2         0.0          0.0              0.000000              0.000000   

   Casino  Castle  Chinese Restaurant  Chocolate Shop  Churrascaria  Circus  \
0     0.0     0.0            0.100000             0.1           0.0     0.0   
1     0.0     0.0            0.083333             0.0           0.0     0.0   
2     0.0     0.0            0.000000             0.0           0.0     0.0   

   Climbing Gym  Clothing Store  Cocktail Bar  Coffee Shop  \
0           0.0             0.0           0.0     0.000000   
1           0.0             0.0           0.0     0.083333   
2           0.0             0.0           0.0     0.000000   

   College Rec Center  Comedy Club  Comfort Food Restaurant  Comic Shop  \
0                 0.0          0.0                      0.0         0.0   
1                 0.0          0.0                      0.0         0.0   
2                 0.0          0.0                      0.0         0.0   

   Concert Hall  Convenience Store  Cosmetics Shop  Creperie  \
0           0.0                0.0             0.0       0.0   
1           0.0                0.0             0.0       0.0   
2      

In [38]:
from sklearn import preprocessing
x = toronto_grouped[['Pedestrian_dens']].values.astype(float)

# Create a minimum and maximum processor object
min_max_scaler = preprocessing.MinMaxScaler()

# Create an object to transform the data to fit minmax processor
x_scaled = min_max_scaler.fit_transform(x)

# Run the normalizer on the dataframe
toronto_grouped['Pedestrian_dens'] = pd.DataFrame(x_scaled)
toronto_grouped.head(3)

Neighborhood  Zoo Exhibit  Adult Boutique  \
0               Agincourt North           0.0             0.0   
1  Agincourt South-Malvern West           0.0             0.0   
2                     Alderwood           0.0             0.0   

   Afghan Restaurant  African Restaurant  American Restaurant  Aquarium  \
0                0.0                 0.0                  0.0       0.0   
1                0.0                 0.0                  0.0       0.0   
2                0.0                 0.0                  0.0       0.0   

   Art Gallery  Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0          0.0                  0.0          0.000000                 0.0   
1          0.0                  0.0          0.041667                 0.0   
2          0.0                  0.0          0.000000                 0.0   

   Auto Dealership  Automotive Shop  BBQ Joint  Bagel Shop    Bakery  Bank  \
0              0.0              0.0        0.0         0.0  0.000000   0.0   
1              0.0              0.0        0.0         0.0  0.041667   0.0   
2              0.0              0.0        0.0         0.0  0.000000   0.0   

   Bar  Baseball Field  Baseball Stadium  Basketball Court  \
0  0.0             0.0               0.0               0.0   
1  0.0             0.0               0.0               0.0   
2  0.0             0.0               0.0               0.0   

   Basketball Stadium  Beach  Beer Bar  Beer Store  Big Box Store  Bike Shop  \
0                 0.0    0.0       0.0         0.0            0.0        0.0   
1                 0.0    0.0       0.0         0.0            0.0        0.0   
2                 0.0    0.0       0.0         0.0            0.0        0.0   

   Bistro  Bookstore  Boutique  Bowling Alley  Brazilian Restaurant  \
0     0.0        0.0       0.0            0.0                   0.0   
1     0.0        0.0       0.0            0.0                   0.0   
2     0.0        0.0       0.0            0.0                   0.0   

   Breakfast Spot  Brewery  Bridal Shop  Bridge  Bubble Tea Shop  Building  \
0        0.000000      0.0          0.0     0.0              0.0       0.0   
1        0.083333      0.0          0.0     0.0              0.0       0.0   
2        0.000000      0.0          0.0     0.0              0.0       0.0   

   Burger Joint  Burrito Place  Butcher  Café  Cajun / Creole Restaurant  \
0           0.0            0.0      0.0   0.0                        0.0   
1           0.0            0.0      0.0   0.0                        0.0   
2           0.0            0.0      0.0   0.0                        0.0   

   Campground  Candy Store  Cantonese Restaurant  Caribbean Restaurant  \
0         0.0          0.0              0.000000              0.100000   
1         0.0          0.0              0.041667              0.083333   
2         0.0          0.0              0.000000              0.000000   

   Casino  Castle  Chinese Restaurant  Chocolate Shop  Churrascaria  Circus  \
0     0.0     0.0            0.100000             0.1           0.0     0.0   
1     0.0     0.0            0.083333             0.0           0.0     0.0   
2     0.0     0.0            0.000000             0.0           0.0     0.0   

   Climbing Gym  Clothing Store  Cocktail Bar  Coffee Shop  \
0           0.0             0.0           0.0     0.000000   
1           0.0             0.0           0.0     0.083333   
2           0.0             0.0           0.0     0.000000   

   College Rec Center  Comedy Club  Comfort Food Restaurant  Comic Shop  \
0                 0.0          0.0                      0.0         0.0   
1                 0.0          0.0                      0.0         0.0   
2                 0.0          0.0                      0.0         0.0   

   Concert Hall  Convenience Store  Cosmetics Shop  Creperie  \
0           0.0                0.0             0.0       0.0   
1           0.0                0.0             0.0       0.0   
2      

creating  k mean cluster based in type venues in each Neighborhood  and the traffic data 

In [39]:
# set number of clusters
kclusters = 10

toronto_grouped_clustering = toronto_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_.shape


(140,)

reconstructing  the datafame  

In [40]:

final=gdf.sort_values(by=['Neighbourhood']).reset_index(drop=True)
final.head(3)

AREA_S_CD                  Neighbourhood  \
0       129               Agincourt North    
1       128  Agincourt South-Malvern West    
2       020                     Alderwood    

                                            geometry   Latitude  longitude  \
0  POLYGON ((-79.242127455 43.802472003, -79.2431...  43.805441 -79.266712   
1  POLYGON ((-79.25497985600001 43.781222538, -79...  43.788657 -79.265611   
2  POLYGON ((-79.548657455 43.590216104, -79.5487...  43.604937 -79.541611   

   Vehicle_density  Pedestrian_dens  
0           307890            16112  
1           512046            16397  
2           141727             2341

In [41]:
toronto_merged = final

# add clustering labels
toronto_merged['Cluster Labels'] = kmeans.labels_

# merge toronto_grouped with toronto_data to add latitude/longitude for each Neighbourhood neighborhood neighborhoods
toronto_merged = toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighbourhood')

toronto_merged.head() # check the last columns!

AREA_S_CD                  Neighbourhood  \
0       129               Agincourt North    
1       128  Agincourt South-Malvern West    
2       020                     Alderwood    
3       095                         Annex    
4       042             Banbury-Don Mills    

                                            geometry   Latitude  longitude  \
0  POLYGON ((-79.242127455 43.802472003, -79.2431...  43.805441 -79.266712   
1  POLYGON ((-79.25497985600001 43.781222538, -79...  43.788657 -79.265611   
2  POLYGON ((-79.548657455 43.590216104, -79.5487...  43.604937 -79.541611   
3  POLYGON ((-79.39414141500001 43.668720261, -79...  43.671585 -79.404000   
4  POLYGON ((-79.33055472300001 43.73978988, -79....  43.737658 -79.349720   

   Vehicle_density  Pedestrian_dens  Cluster Labels  \
0           307890            16112               1   
1           512046            16397               6   
2           141727             2341               3   
3           370226           130702               6   
4           556039            19987               6   

       1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0       Fast Food Restaurant        Sandwich Place        Discount Store   
1       Gym / Fitness Center           Coffee Shop    Chinese Restaurant   
2             Discount Store                   Pub   Moroccan Restaurant   
3                       Café    Italian Restaurant         Grocery Store   
4  Middle Eastern Restaurant                  Park          Burger Joint   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0  Caribbean Restaurant    Chinese Restaurant     Indian Restaurant   
1  Caribbean Restaurant        Breakfast Spot     Indian Restaurant   
2                   Gym         Grocery Store           Pizza Place   
3                 Hotel                  Park          Dessert Shop   
4                  Café        Ice Cream Shop   Japanese Restaurant   

  7th Most Common Venue      8th Most Common Venue 9th Most Common Venue  \
0        Chocolate Shop                  Juice Bar           Supermarket   
1              Pharmacy                 Restaurant                 Diner   
2     Electronics Store                 Donut Shop   Dumpling Restaurant   
3            Restaurant  Middle Eastern Restaurant    Mexican Restaurant   
4           Supermarket                Coffee Shop        Clothing Store   

        10th Most Common Venue  
0                     Pharmacy  
1               Sandwich Place  
2  Eastern European Restaurant  
3     Mediterranean Restaurant  
4                Shopping Mall

visualizing the result

In [43]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Latitude'], toronto_merged['longitude'], toronto_merged['Neighbourhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

print the cluster result 

In [44]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 0, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Neighbourhood  Vehicle_density  Pedestrian_dens  Cluster Labels  \
127  Weston-Pellam Park             79759             8244               0   

    1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
127  Brazilian Restaurant            Comic Shop                 Field   

    4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
127  Fast Food Restaurant        Farmers Market                  Farm   

    7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
127    Falafel Restaurant            Eye Doctor           Event Space   

    10th Most Common Venue  
127   Ethiopian Restaurant

#### Cluster 2

In [45]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 1, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Neighbourhood  Vehicle_density  Pedestrian_dens  \
0                      Agincourt North            307890            16112   
13                         Black Creek            205388            21718   
15                Briar Hill-Belgravia            155278            12377   
18                 Brookhaven-Amesbury            173898            13328   
20                  Caledonia-Fairbank            102319            13547   
22              Centennial Scarborough             64342             2209   
26                          Cliffcrest            181370             5802   
37                       Eglinton East            213282            14837   
38                    Elms-Old Rexdale            163930             5694   
40      Eringate-Centennial-West Deane            141431             3045   
45              Glenfield-Jane Heights            257859            13157   
47                           Guildwood             31663             1347   
48                          Henry Farm            138415             6659   
54                       Humber Summit            335650            10655   
56                  Humewood-Cedarvale             72029             3418   
61                        Kennedy Park            164672             8032   
63       Kingsview Village-The Westway            278902             8908   
75                       Markland Wood            130773             3227   
78                         Morningside            118812             5405   
81   Mount Olive-Silverstone-Jamestown            256849            20037   
96                Pelmo Park-Humberlea            149907             2597   
99                  Princess-Rosethorn             73921             1450   
101                    Rexdale-Kipling            124235             5110   
108                Scarborough Village            202944            11492   
115                      Taylor-Massey             49105             6431   
117       Thistletown-Beaumond Heights            150764             8562   
121                   Victoria Village            177553             6387   
125                Westminster-Branson             70750             2885   
126                             Weston            172982            15563   
131   Willowridge-Martingrove-Richview            274093             7371   
134                   Woodbine-Lumsden             24828             1594   

     Cluster Labels      1st Most Common Venue      2nd Most Common Venue  \
0                 1       Fast Food Restaurant             Sandwich Place   
13                1                      Hotel       Kitchen Supply Store   
15                1     Furniture / Home Store        Japanese Restaurant   
18                1                Coffee Shop                    Brewery   
20                1                   Pharmacy                        Zoo   
22                1       Fast Food Restaurant                 Beer Store   
26                1                       Park             Ice Cream Shop   
37                1             Ice Cream Shop             Sandwich Place   
38                1       Fast Food Restaurant              Big Box Store   
40                1                       Park             Sandwich Place   
45                1                Coffee Shop                Pizza Place   
47                1                        Pub                 Sports Bar   
48                1  Middle Eastern Restaurant         Chinese Restaurant   
54                1                       Bank       Fast Food Restaurant   
56                1                      Field  Middle Eastern Restaurant   
61                1                 Beer Store       Fast Food Restaurant   
63                1                Coffee Shop                Pizza Place   
75                1                 Beer Store             Sandwich Place   
78                1                Coffee Shop                        Pub   
81                1  

#### Cluster 3

In [46]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 2, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Neighbourhood  Vehicle_density  Pedestrian_dens  Cluster Labels  \
41   Etobicoke West Mall            133865             5449               2   
43     Forest Hill North            185660            13120               2   
49       High Park North             78797            11864               2   
55            Humbermede            168643             5411               2   
57               Ionview            176532             8330               2   
80          Mount Dennis            134367             9963               2   
92       Oakwood Village            117200            13048               2   
100          Regent Park             84891            19737               2   

    1st Most Common Venue 2nd Most Common Venue  3rd Most Common Venue  \
41         Farmers Market           Coffee Shop                    Zoo   
43                 Bakery           Coffee Shop       Doner Restaurant   
49            Coffee Shop    Italian Restaurant                  Diner   
55            Coffee Shop                  Café  Vietnamese Restaurant   
57            Coffee Shop    Chinese Restaurant                    Zoo   
80            Coffee Shop                   Zoo       Doner Restaurant   
92            Coffee Shop  Caribbean Restaurant                    Zoo   
100           Coffee Shop                   Zoo       Doner Restaurant   

    4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
41       Doner Restaurant  Fast Food Restaurant                  Farm   
43   Fast Food Restaurant        Farmers Market                  Farm   
49                   Park            Soup Place            Eye Doctor   
55         Sandwich Place                   Zoo   Egyptian Restaurant   
57       Doner Restaurant  Fast Food Restaurant        Farmers Market   
80   Fast Food Restaurant        Farmers Market                  Farm   
92       Doner Restaurant  Fast Food Restaurant        Farmers Market   
100  Fast Food Restaurant        Farmers Market                  Farm   

    7th Most Common Venue 8th Most Common Venue        9th Most Common Venue  \
41     Falafel Restaurant            Eye Doctor                  Event Space   
43     Falafel Restaurant            Eye Doctor                  Event Space   
49            Event Space  Ethiopian Restaurant                      Dog Run   
55             Donut Shop   Dumpling Restaurant  Eastern European Restaurant   
57                   Farm    Falafel Restaurant                   Eye Doctor   
80     Falafel Restaurant            Eye Doctor                  Event Space   
92                   Farm    Falafel Restaurant                   Eye Doctor   
100    Falafel Restaurant            Eye Doctor                  Event Space   

    10th Most Common Venue  
41    Ethiopian Restaurant  
43    Ethiopian Restaurant  
49       Electronics Store  
55    Ethiopian Restaurant  
57             Event Space  
80    Ethiopian Restaurant  
92             Event Space  
100   Ethiopian Restaurant

#### Cluster 4

In [47]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 3, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Neighbourhood  Vehicle_density  Pedestrian_dens  \
2                              Alderwood            141727             2341   
5                         Bathurst Manor            312779             8381   
8                  Bayview Woods-Steeles            101357             3078   
10               Beechborough-Greenbrook            177560             6029   
12                 Birchcliffe-Cliffside            232623            12008   
14                           Blake-Jones             26837             7261   
16     Bridle Path-Sunnybrook-York Mills            225849             5466   
19       Cabbagetown-South St.James Town            142395            42445   
21                             Casa Loma            157121            19959   
25                          Clanton Park            233484             7096   
27                Corso Italia-Davenport            125357            30710   
28                              Danforth             81141            21956   
32   Dovercourt-Wallace Emerson-Junction            296591            33397   
34                        Dufferin Grove             66553            19423   
35                     East End-Danforth            236605            32582   
36              Edenbridge-Humber Valley            186180             2744   
39                   Englemount-Lawrence            110629             6504   
42                       Flemingdon Park            171670            12860   
44                     Forest Hill South            111982            10522   
46                     Greenwood-Coxwell            109468            16530   
50                     High Park-Swansea            238369            29709   
51                        Highland Creek            112571             7667   
53              Humber Heights-Westmount            159074             5223   
59                         Junction Area            304567            29337   
60              Keelesdale-Eglinton West            119994            13525   
62                  Kensington-Chinatown            296408           231251   
64                        Kingsway South             79613             2084   
66                    Lambton Baby Point             69191             2297   
67                      Lansing-Westgate            256594            19683   
68                   Lawrence Park North            116813            21695   
69                   Lawrence Park South            160434             9481   
70                    Leaside-Bennington            267974            14322   
71                       Little Portugal            106956            20856   
72                           Long Branch             69413             5812   
77   Mimico (includes Humber Bay Shores)            285833            16254   
82                   Mount Pleasant East            271234            31040   
83                   Mount Pleasant West            161261            80425   
84                           New Toronto            124642            14051   
86                      Newtonbrook West            157995             9228   
87                               Niagara            297861            32344   
88                       North Riverdale             88019            44536   
90                     O'Connor-Parkview            129479             4952   
91                              Oakridge            148279            14712   
94               Palmerston-Little Italy            173759            56007   
95                     Parkwoods-Donalda            191717             6491   
97              Playter Estates-Danforth             18248             4048   
98                         Pleasant View            148156             5113   
102                    Rockcliffe-Smythe            195843             9800   
103                         Roncesvalles            124966            32827   
104                  Rosedale-Moore Park            313629            66412   

#### Cluster 5

In [48]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 4, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Neighbourhood  Vehicle_density  Pedestrian_dens  \
58   Islington-City Centre West           1025885            25531   
124      West Humber-Clairville            871743            18900   
128            Wexford/Maryvale           1014330            37811   
132                      Woburn            726732            33590   
138     York University Heights            725619            43226   

     Cluster Labels      1st Most Common Venue      2nd Most Common Venue  \
58                4               Burger Joint                Coffee Shop   
124               4                Coffee Shop                      Hotel   
128               4  Middle Eastern Restaurant               Burger Joint   
132               4                Coffee Shop         Chinese Restaurant   
138               4                Coffee Shop  Middle Eastern Restaurant   

    3rd Most Common Venue   4th Most Common Venue 5th Most Common Venue  \
58                 Bakery  Furniture / Home Store         Grocery Store   
124  Fast Food Restaurant              Steakhouse   American Restaurant   
128           Coffee Shop    Fast Food Restaurant        Clothing Store   
132     Indian Restaurant    Fast Food Restaurant                  Bank   
138         Grocery Store          Sandwich Place        Tennis Stadium   

        6th Most Common Venue 7th Most Common Venue  \
58         Turkish Restaurant      Department Store   
124  Mediterranean Restaurant          Burger Joint   
128               Supermarket          Liquor Store   
132                     Hotel           Pizza Place   
138               Pizza Place              Pharmacy   

         8th Most Common Venue  9th Most Common Venue 10th Most Common Venue  
58   Middle Eastern Restaurant            Yoga Studio             Restaurant  
124               Skating Rink            Pizza Place       Sushi Restaurant  
128   Mediterranean Restaurant             Steakhouse    Japanese Restaurant  
132                   Pharmacy  Vietnamese Restaurant             Steakhouse  
138             Discount Store            Supermarket         Massage Studio

In [49]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 6, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Neighbourhood  Vehicle_density  Pedestrian_dens  \
1    Agincourt South-Malvern West            512046            16397   
3                           Annex            370226           130702   
4               Banbury-Don Mills            556039            19987   
7                 Bayview Village            357816             9863   
9            Bedford Park-Nortown            585768            28967   
11                        Bendale            623539            17194   
24            Clairlea-Birchmount            475237            19719   
30             Don Valley Village            321730            15602   
31                    Dorset Park            422958            15461   
33           Downsview-Roding-CFB            602924            29128   
52              Hillcrest Village            317720            21245   
65                     L'Amoreaux            531886            26489   
73                        Malvern            364576            17463   
76                       Milliken            534059            14349   
79                      Moss Park            382973           120328   
85               Newtonbrook East            414909            36456   
105                         Rouge            455481            12015   
110               South Riverdale            390386            60638   
111          St.Andrew-Windfields            388202            10586   
113           Stonegate-Queensway            374463            14620   
114        Tam O'Shanter-Sullivan            326790            13466   
123                     West Hill            324588            15708   
129               Willowdale East            430006            69355   
139            Yorkdale-Glen Park            463325            27812   

     Cluster Labels      1st Most Common Venue 2nd Most Common Venue  \
1                 6       Gym / Fitness Center           Coffee Shop   
3                 6                       Café    Italian Restaurant   
4                 6  Middle Eastern Restaurant                  Park   
7                 6                Coffee Shop          Liquor Store   
9                 6             Hardware Store          Gourmet Shop   
11                6             Clothing Store    Chinese Restaurant   
24                6               Burger Joint         Burrito Place   
30                6                     Bakery  Caribbean Restaurant   
31                6                Coffee Shop  Gym / Fitness Center   
33                6      Vietnamese Restaurant           Coffee Shop   
52                6         Chinese Restaurant      Sushi Restaurant   
65                6       Caribbean Restaurant                Bakery   
73                6                Pizza Place    Chinese Restaurant   
76                6         Chinese Restaurant              Tea Room   
79                6                Coffee Shop    Italian Restaurant   
85                6                Coffee Shop         Burrito Place   
105               6                Zoo Exhibit                  Park   
110               6                Coffee Shop                 Beach   
111               6                 Steakhouse    Persian Restaurant   
113               6         Italian Restaurant           Coffee Shop   
114               6         Chinese Restaurant           Coffee Shop   
123               6                Pizza Place  Fast Food Restaurant   
129               6           Ramen Restaurant                  Café   
139               6             Clothing Store           Coffee Shop   

      3rd Most Common Venue   4th Most Common Venue    5th Most Common Venue  \
1        Chinese Restaurant    Caribbean Restaurant           Breakfast Spot   
3             Grocery Store                   Hotel                     Park   
4              Burger Joint                    Café           Ice Cream Shop   
7            Breakfast Spot    Outdoor Supply Store  Scandinavian Restaurant   
9                  

In [50]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 7, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Neighbourhood  Vehicle_density  Pedestrian_dens  Cluster Labels  \
29  Danforth East York            123220            12311               7   

   1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
29        Farmers Market                   Zoo      Doner Restaurant   

   4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
29  Fast Food Restaurant                  Farm    Falafel Restaurant   

   7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
29            Eye Doctor           Event Space  Ethiopian Restaurant   

   10th Most Common Venue  
29      Electronics Store

In [51]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 8, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Neighbourhood  Vehicle_density  Pedestrian_dens  Cluster Labels  \
17  Broadview North             70245            11854               8   
74       Maple Leaf            182691            10763               8   
93    Old East York            185164             4152               8   

   1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
17                Bakery   Filipino Restaurant  Fast Food Restaurant   
74                Bakery             Pet Store               Dog Run   
93                Bakery        Sandwich Place          Gourmet Shop   

   4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
17        Farmers Market                  Farm    Falafel Restaurant   
74        Farmers Market                  Farm    Falafel Restaurant   
93               Dog Run        Farmers Market                  Farm   

   7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
17            Eye Doctor           Event Space  Ethiopian Restaurant   
74            Eye Doctor           Event Space  Ethiopian Restaurant   
93    Falafel Restaurant            Eye Doctor           Event Space   

   10th Most Common Venue  
17      Electronics Store  
74      Electronics Store  
93   Ethiopian Restaurant

In [52]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 9, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Neighbourhood  Vehicle_density  Pedestrian_dens  \
6                  Bay Street Corridor            554737           600095   
23               Church-Yonge Corridor            435106           540523   
122  Waterfront Communities-The Island            916197           486602   

     Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
6                 9           Coffee Shop                   Gym   
23                9             Gastropub   Japanese Restaurant   
122               9           Coffee Shop                  Park   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
6         Bubble Tea Shop                  Café             Bookstore   
23        Thai Restaurant          Concert Hall            Restaurant   
122    Italian Restaurant                 Hotel           Yoga Studio   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
6                    Park            Restaurant             Gastropub   
23          Burrito Place        Breakfast Spot                  Café   
122        Farmers Market            Steakhouse   Sporting Goods Shop   

    9th Most Common Venue 10th Most Common Venue  
6                  Museum          Shopping Mall  
23              Bookstore            Supermarket  
122          Dessert Shop       Baseball Stadium

In [53]:
def plot_gdf_folium(gdf, center):
    m = folium.Map(center, zoom_start=10, tiles='OpenStreetMap')
    folium.GeoJson(gdf).add_to(m)
    return m

In [56]:
center=(43.671585, -79.404000)
plot_gdf_folium(gdf, center)